In [6]:
import pandas as pd
import os
import numpy as np
import seaborn as sns 
import plotly.express as px
from sklearn.decomposition import PCA
import plotly.graph_objects as go
import plotly.express as px
import matplotlib.cm as cm
from pathlib import Path


# Use the parent directory of this file for results
# results_dir = os.getcwd()
results_dir = "/net/trapnell/vol1/home/mdcolon/proj/morphseq/results/mcolon/20250919"
data_dir = os.path.join(results_dir, "data")
plot_dir = os.path.join(results_dir, "plots")

print(f"Results directory: {results_dir}")
os.makedirs(plot_dir, exist_ok=True)
os.makedirs(data_dir, exist_ok=True)


morphseq_root = os.environ.get('MORPHSEQ_REPO_ROOT')
morphseq_root = "/net/trapnell/vol1/home/mdcolon/proj/morphseq"
print(f"MORPHSEQ_REPO_ROOT: {morphseq_root}")
os.chdir(morphseq_root)

from src.functions.embryo_df_performance_metrics import *
from src.functions.spline_morph_spline_metrics import *



Results directory: /net/trapnell/vol1/home/mdcolon/proj/morphseq/results/mcolon/20250919
MORPHSEQ_REPO_ROOT: /net/trapnell/vol1/home/mdcolon/proj/morphseq


In [7]:
combined_df = pd.read_csv("/net/trapnell/vol1/home/mdcolon/proj/morphseq/results/mcolon/20250920/data/qc_staged_Titration_experiments_combined_20250912_20250711.csv")

/tmp/153775.1.trapnell-login.q/ipykernel_1823719/2767086088.py:1: DtypeWarning:

Columns (34,68) have mixed types. Specify dtype option on import or set low_memory=False.



In [8]:
# combined_df = combined_df[combined_df["predicted_stage_hpf"] >=18 ]

# combined_df = apply_pca_if_needed(combined_df, n_components=3)

# evaluating flag occurance in tricane titration experiment

> so i did an experimentt where i changed the
  ititration of tricane and imaged for a
  long time. I hypothesized that higher
  levels would cause death but no moviement,
  low levels would cause less death but worse
  quality due to higher movement, we use the
  tricane to keep themebryos still for
  imaging )and in methyl celllaose), I want
  to look at the trends of the flags
  throughout the experiemnt for all te
  embryos.  



  first we will look at the dead flag, and
  look at it on  a per embryo bassis over
  predicted stge_hpf, coloring by
  chem_n_genotype AND THEN Ffinally the
  average percent of the dead_flag overtime
  to look at gross trinds, plot this in
  plotly so i can see indivudal embryo_ids as
  i hover over them.

In [9]:
# Filter data for tricaine analysis including wildtype control
qc_staged_df = combined_df.copy()
print("Original data shape:", qc_staged_df.shape)
print("Unique chem_n_genotype values:", qc_staged_df['chem_n_genotype'].unique())

# Filter to include tricaine concentrations + wildtype tmem67 as control
tricane_conditions = qc_staged_df['chem_perturbation'].str.startswith('tri_', na=False)
wildtype_control = qc_staged_df['chem_n_genotype'] == 'nan_tmem67_wildtype'

filtered_df = qc_staged_df[tricane_conditions | wildtype_control].copy()

print(f"\nFiltered data shape: {filtered_df.shape}")
print("Conditions included:")
print(filtered_df['chem_n_genotype'].value_counts().sort_index())

Original data shape: (28625, 76)
Unique chem_n_genotype values: ['tri_1-15_wik-ab' 'tri_1-20_wik-ab' 'tri_1-25_wik-ab' 'tri_1-30_wik-ab'
 'tri_1-35_wik-ab' 'tri_1-40_wik-ab' 'tri_0_wik-ab'
 'nan_tmem67_heterozygote' 'nan_tmem67_homozygous' 'nan_tmem67_wildtype']

Filtered data shape: (16095, 76)
Conditions included:
chem_n_genotype
nan_tmem67_wildtype    4117
tri_0_wik-ab           1017
tri_1-15_wik-ab         904
tri_1-20_wik-ab        1921
tri_1-25_wik-ab        2260
tri_1-30_wik-ab        2147
tri_1-35_wik-ab        1808
tri_1-40_wik-ab        1921
Name: count, dtype: int64


In [10]:
# 2. Population survival trends - average % dead over time
# Bin time points and calculate average % dead for each condition

import numpy as np

# Create time bins for averaging
time_bins = np.arange(
    filtered_df['predicted_stage_hpf'].min(), 
    filtered_df['predicted_stage_hpf'].max() + 5, 
    5  # 5 hpf bins
)

fig2 = go.Figure()

# Calculate average % dead for each condition over time bins
for condition in sorted(conditions):
    condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
    
    bin_centers = []
    avg_dead_pct = []
    sample_sizes = []
    
    for i in range(len(time_bins) - 1):
        bin_start, bin_end = time_bins[i], time_bins[i + 1]
        bin_data = condition_data[
            (condition_data['predicted_stage_hpf'] >= bin_start) & 
            (condition_data['predicted_stage_hpf'] < bin_end)
        ]
        
        if len(bin_data) > 0:
            bin_centers.append((bin_start + bin_end) / 2)
            dead_pct = (bin_data['dead_flag2'].sum() / len(bin_data)) * 100
            avg_dead_pct.append(dead_pct)
            sample_sizes.append(len(bin_data))
    
    # Create hover text for line plot
    hover_text = [
        f"<b>Condition: {condition}</b><br>"
        f"Time bin: {center:.1f} hpf<br>"
        f"% Dead: {pct:.1f}%<br>"
        f"Sample size: {n} observations"
        for center, pct, n in zip(bin_centers, avg_dead_pct, sample_sizes)
    ]
    
    fig2.add_trace(
        go.Scatter(
            x=bin_centers,
            y=avg_dead_pct,
            mode='lines+markers',
            line=dict(color=color_map[condition], width=3),
            marker=dict(size=8),
            name=condition,
            hovertemplate='%{text}<extra></extra>',
            text=hover_text
        )
    )

fig2.update_layout(
    title="Population Survival Trends: Average % Dead Over Time",
    xaxis_title="Predicted Stage (hpf)",
    yaxis_title="Average % Dead",
    height=600,
    hovermode='closest',
    yaxis=dict(range=[0, 100])  # Set y-axis to 0-100%
)

# Save the plot
fig2.write_html(os.path.join(plot_dir, "population_survival_trends.html"))
fig2.show()

In [11]:
# 3. Additional quality flags analysis
# Analyze sam2_flag and  to validate movement vs quality hypothesis

quality_flags = ['sam2_qc_flag', 'frame_flag', 'no_yolk_flag', 'use_embryo_flag']

# Create subplots for each quality flag
from plotly.subplots import make_subplots

fig3 = make_subplots(
    rows=2, cols=2,
    subplot_titles=quality_flags,
    specs=[[{'secondary_y': False}, {'secondary_y': False}],
           [{'secondary_y': False}, {'secondary_y': False}]]
)

for i, flag in enumerate(quality_flags):
    row = (i // 2) + 1
    col = (i % 2) + 1
    
    for condition in sorted(conditions):
        condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
        
        bin_centers = []
        avg_flag_pct = []
        sample_sizes = []
        
        for j in range(len(time_bins) - 1):
            bin_start, bin_end = time_bins[j], time_bins[j + 1]
            bin_data = condition_data[
                (condition_data['predicted_stage_hpf'] >= bin_start) & 
                (condition_data['predicted_stage_hpf'] < bin_end)
            ]
            
            if len(bin_data) > 0:
                bin_centers.append((bin_start + bin_end) / 2)
                flag_pct = (bin_data[flag].sum() / len(bin_data)) * 100
                avg_flag_pct.append(flag_pct)
                sample_sizes.append(len(bin_data))
        
        # Create hover text
        hover_text = [
            f"<b>Condition: {condition}</b><br>"
            f"Time bin: {center:.1f} hpf<br>"
            f"% {flag}: {pct:.1f}%<br>"
            f"Sample size: {n} observations"
            for center, pct, n in zip(bin_centers, avg_flag_pct, sample_sizes)
        ]
        
        fig3.add_trace(
            go.Scatter(
                x=bin_centers,
                y=avg_flag_pct,
                mode='lines+markers',
                line=dict(color=color_map[condition], width=2),
                marker=dict(size=4),
                name=condition,
                showlegend=(i == 0),  # Only show legend for first subplot
                hovertemplate='%{text}<extra></extra>',
                text=hover_text
            ),
            row=row, col=col
        )

# Update layout
fig3.update_layout(
    title="Quality Flag Trends Over Time by Tricaine Concentration",
    height=800,
    hovermode='closest'
)

# Update x and y axis labels
for i in range(1, 3):
    for j in range(1, 3):
        fig3.update_xaxes(title_text="Predicted Stage (hpf)", row=i, col=j)
        fig3.update_yaxes(title_text="% Flagged", row=i, col=j, range=[0, 100])

# Save the plot
fig3.write_html(os.path.join(plot_dir, "quality_flags_analysis.html"))
fig3.show()

In [12]:
# Summary statistics for tricaine concentration effects
print("=== TRICAINE TITRATION EXPERIMENT SUMMARY ===\n")

print("Data Overview:")
print(f"Total observations: {len(filtered_df)}")
print(f"Time range: {filtered_df['predicted_stage_hpf'].min():.1f} - {filtered_df['predicted_stage_hpf'].max():.1f} hpf")
print(f"Number of unique embryos: {filtered_df['embryo_id'].nunique()}")

print("\nConditions analyzed:")
condition_summary = filtered_df.groupby('chem_n_genotype').agg({
    'embryo_id': 'nunique',
    'dead_flag2': ['count', 'sum', 'mean'],
    'focus_flag': 'mean',
    'bubble_flag': 'mean'
}).round(3)

condition_summary.columns = ['N_embryos', 'N_observations', 'N_dead', 'Pct_dead', 'Pct_focus_flag', 'Pct_bubble_flag']
condition_summary['Pct_dead'] = (condition_summary['Pct_dead'] * 100).round(1)
condition_summary['Pct_focus_flag'] = (condition_summary['Pct_focus_flag'] * 100).round(1)
condition_summary['Pct_bubble_flag'] = (condition_summary['Pct_bubble_flag'] * 100).round(1)

print(condition_summary)

print(f"\nPlots saved to: {plot_dir}")
print("- individual_embryo_survival_trajectories.html")
print("- population_survival_trends.html") 
print("- quality_flags_analysis.html")

=== TRICAINE TITRATION EXPERIMENT SUMMARY ===

Data Overview:
Total observations: 16095
Time range: 7.0 - 127.9 hpf
Number of unique embryos: 129

Conditions analyzed:
                     N_embryos  N_observations  N_dead  Pct_dead  \
chem_n_genotype                                                    
nan_tmem67_wildtype         23            4117     927      22.5   
tri_0_wik-ab                 9            1017     705      69.3   
tri_1-15_wik-ab              8             904     737      81.5   
tri_1-20_wik-ab             17            1921    1557      81.1   
tri_1-25_wik-ab             20            2260     909      40.2   
tri_1-30_wik-ab             19            2147    1267      59.0   
tri_1-35_wik-ab             16            1808    1254      69.4   
tri_1-40_wik-ab             17            1921    1097      57.1   

                     Pct_focus_flag  Pct_bubble_flag  
chem_n_genotype                                       
nan_tmem67_wildtype            19.7      

In [13]:
# Examine sam2_qc_flags to understand individual flag types
print("=== SAM2 QC FLAGS ANALYSIS ===\n")

print("Unique sam2_qc_flags values:")
sam2_flags_counts = filtered_df['sam2_qc_flags'].value_counts()
print(sam2_flags_counts.head(20))

print(f"\nTotal unique flag combinations: {len(sam2_flags_counts)}")

# Look at some examples to understand the structure
print("\nSample of sam2_qc_flags values:")
sample_flags = filtered_df['sam2_qc_flags'].dropna().unique()[:10]
for flag in sample_flags:
    print(f"'{flag}'")

# Check if flags are comma-separated or have other delimiters
print("\nChecking flag structure...")
non_null_flags = filtered_df['sam2_qc_flags'].dropna()
if len(non_null_flags) > 0:
    sample_flag = non_null_flags.iloc[0]
    print(f"Sample flag: '{sample_flag}'")
    print(f"Contains comma: {',' in str(sample_flag)}")
    print(f"Contains semicolon: {';' in str(sample_flag)}")
    print(f"Contains pipe: {'|' in str(sample_flag)}")
    print(f"Contains space: {' ' in str(sample_flag)}")

=== SAM2 QC FLAGS ANALYSIS ===

Unique sam2_qc_flags values:
sam2_qc_flags
HIGH_SEGMENTATION_VAR_SNIP                                    1517
DISCONTINUOUS_MASK                                            1360
MASK_ON_EDGE                                                   469
HIGH_SEGMENTATION_VAR_SNIP,DISCONTINUOUS_MASK                   88
HIGH_SEGMENTATION_VAR_SNIP,MASK_ON_EDGE                         41
HIGH_SEGMENTATION_VAR_SNIP,MASK_ON_EDGE,DISCONTINUOUS_MASK       2
HIGH_SEGMENTATION_VAR_SNIP,SMALL_MASK                            1
Name: count, dtype: int64

Total unique flag combinations: 7

Sample of sam2_qc_flags values:
'DISCONTINUOUS_MASK'
'HIGH_SEGMENTATION_VAR_SNIP'
'HIGH_SEGMENTATION_VAR_SNIP,DISCONTINUOUS_MASK'
'HIGH_SEGMENTATION_VAR_SNIP,SMALL_MASK'
'MASK_ON_EDGE'
'HIGH_SEGMENTATION_VAR_SNIP,MASK_ON_EDGE'
'HIGH_SEGMENTATION_VAR_SNIP,MASK_ON_EDGE,DISCONTINUOUS_MASK'

Checking flag structure...
Sample flag: 'DISCONTINUOUS_MASK'
Contains comma: False
Contains semicolon: Fa

In [14]:
# Parse individual SAM2 QC flags and analyze their distribution
import re

def parse_sam2_flags(flag_string):
    """Parse sam2_qc_flags string into individual flag types"""
    if pd.isna(flag_string) or flag_string == '' or flag_string == 'False':
        return []
    
    # Convert to string and clean
    flag_string = str(flag_string).strip()
    
    # Try different delimiters
    if ',' in flag_string:
        flags = [f.strip() for f in flag_string.split(',')]
    elif ';' in flag_string:
        flags = [f.strip() for f in flag_string.split(';')]
    elif '|' in flag_string:
        flags = [f.strip() for f in flag_string.split('|')]
    else:
        # Single flag or space-separated
        flags = [f.strip() for f in flag_string.split()]
    
    # Filter out empty strings and common non-flag values
    flags = [f for f in flags if f and f not in ['False', 'True', 'None', 'nan']]
    return flags

# Parse all flags
filtered_df['sam2_flags_parsed'] = filtered_df['sam2_qc_flags'].apply(parse_sam2_flags)

# Get all unique individual flag types
all_individual_flags = []
for flag_list in filtered_df['sam2_flags_parsed']:
    all_individual_flags.extend(flag_list)

individual_flag_counts = pd.Series(all_individual_flags).value_counts()
print("Individual SAM2 QC flag types and their frequencies:")
print(individual_flag_counts)

print(f"\nTotal unique individual flag types: {len(individual_flag_counts)}")

# Create binary columns for each flag type
top_flags = individual_flag_counts.head(10).index.tolist()  # Get top 10 most common flags
print(f"\nAnalyzing top {len(top_flags)} most common flags:")
print(top_flags)

# Create binary indicator columns for each flag type
for flag_type in top_flags:
    filtered_df[f'sam2_{flag_type}_flag'] = filtered_df['sam2_flags_parsed'].apply(
        lambda x: flag_type in x if isinstance(x, list) else False
    )

Individual SAM2 QC flag types and their frequencies:
HIGH_SEGMENTATION_VAR_SNIP    1649
DISCONTINUOUS_MASK            1450
MASK_ON_EDGE                   512
SMALL_MASK                       1
Name: count, dtype: int64

Total unique individual flag types: 4

Analyzing top 4 most common flags:
['HIGH_SEGMENTATION_VAR_SNIP', 'DISCONTINUOUS_MASK', 'MASK_ON_EDGE', 'SMALL_MASK']


In [15]:
# Create comprehensive SAM2 QC flags analysis - ADJUSTED FOR ALIVE EMBRYOS ONLY
# Plot trends for each individual SAM2 flag type over time by tricaine concentration
# ONLY analyzing alive embryos to avoid bias from dead embryos

sam2_flag_cols = [f'sam2_{flag}_flag' for flag in top_flags]

# Create a large subplot grid for all SAM2 flags
n_flags = len(top_flags)
n_cols = 3  # 3 columns
n_rows = (n_flags + n_cols - 1) // n_cols  # Ceiling division

fig4 = make_subplots(
    rows=n_rows, cols=n_cols,
    subplot_titles=[f"SAM2: {flag} (Alive Only)" for flag in top_flags],
    vertical_spacing=0.08,
    horizontal_spacing=0.05
)

for i, flag_type in enumerate(top_flags):
    row = (i // n_cols) + 1
    col = (i % n_cols) + 1
    flag_col = f'sam2_{flag_type}_flag'
    
    for condition in sorted(conditions):
        condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
        
        bin_centers = []
        avg_flag_pct = []
        sample_sizes = []
        alive_sample_sizes = []
        
        for j in range(len(time_bins) - 1):
            bin_start, bin_end = time_bins[j], time_bins[j + 1]
            bin_data = condition_data[
                (condition_data['predicted_stage_hpf'] >= bin_start) & 
                (condition_data['predicted_stage_hpf'] < bin_end)
            ]
            
            # FILTER TO ALIVE EMBRYOS ONLY
            alive_bin_data = bin_data[bin_data['dead_flag2'] == False]
            
            if len(alive_bin_data) > 0:
                bin_centers.append((bin_start + bin_end) / 2)
                flag_pct = (alive_bin_data[flag_col].sum() / len(alive_bin_data)) * 100
                avg_flag_pct.append(flag_pct)
                sample_sizes.append(len(bin_data))  # Total in bin
                alive_sample_sizes.append(len(alive_bin_data))  # Alive in bin
        
        # Create hover text with alive vs total info
        hover_text = [
            f"<b>Condition: {condition}</b><br>"
            f"Flag: {flag_type} (Alive Only)<br>"
            f"Time bin: {center:.1f} hpf<br>"
            f"% {flag_type}: {pct:.1f}%<br>"
            f"Alive embryos: {alive_n}<br>"
            f"Total observations: {total_n}"
            for center, pct, alive_n, total_n in zip(bin_centers, avg_flag_pct, alive_sample_sizes, sample_sizes)
        ]
        
        fig4.add_trace(
            go.Scatter(
                x=bin_centers,
                y=avg_flag_pct,
                mode='lines+markers',
                line=dict(color=color_map[condition], width=2),
                marker=dict(size=3),
                name=condition,
                showlegend=(i == 0),  # Only show legend for first subplot
                hovertemplate='%{text}<extra></extra>',
                text=hover_text
            ),
            row=row, col=col
        )

# Update layout
fig4.update_layout(
    title="Individual SAM2 QC Flag Trends Over Time by Tricaine Concentration (Alive Embryos Only)",
    height=300 * n_rows,  # Scale height with number of rows
    hovermode='closest'
)

# Update x and y axis labels
for i in range(1, n_rows + 1):
    for j in range(1, n_cols + 1):
        fig4.update_xaxes(title_text="Stage (hpf)", row=i, col=j)
        fig4.update_yaxes(title_text="% Flagged", row=i, col=j, range=[0, 100])

# Save the plot
fig4.write_html(os.path.join(plot_dir, "sam2_individual_flags_analysis_alive_only.html"))
fig4.show()

In [16]:
# Summary table for SAM2 QC flags by tricaine concentration - ADJUSTED FOR ALIVE EMBRYOS
print("=== SAM2 QC FLAGS SUMMARY BY CONDITION (ALIVE EMBRYOS ONLY) ===\n")

# Create summary table for each SAM2 flag type - ONLY for alive embryos
sam2_summary_data = []

for condition in sorted(conditions):
    condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
    alive_condition_data = condition_data[condition_data['dead_flag2'] == False]
    
    row_data = {
        'condition': condition,
        'n_total_observations': len(condition_data),
        'n_alive_observations': len(alive_condition_data),
        'pct_alive': round((len(alive_condition_data) / len(condition_data)) * 100, 1),
        'n_alive_embryos': alive_condition_data['embryo_id'].nunique()
    }
    
    # Add percentage for each SAM2 flag type - ONLY for alive embryos
    for flag_type in top_flags:
        flag_col = f'sam2_{flag_type}_flag'
        if len(alive_condition_data) > 0:
            pct = (alive_condition_data[flag_col].sum() / len(alive_condition_data)) * 100
            row_data[f'{flag_type}_pct_alive'] = round(pct, 1)
        else:
            row_data[f'{flag_type}_pct_alive'] = 0.0
    
    sam2_summary_data.append(row_data)

sam2_summary_df = pd.DataFrame(sam2_summary_data)
print("SAM2 Flag Percentages by Condition (Alive Embryos Only):")
print(sam2_summary_df.to_string(index=False))

# Create a heatmap of SAM2 flag percentages for alive embryos only
flag_pct_cols = [col for col in sam2_summary_df.columns if col.endswith('_pct_alive')]
heatmap_data = sam2_summary_df[['condition'] + flag_pct_cols].set_index('condition')

fig5 = go.Figure(data=go.Heatmap(
    z=heatmap_data.values,
    x=[col.replace('_pct_alive', '') for col in heatmap_data.columns],
    y=heatmap_data.index,
    colorscale='Reds',
    text=heatmap_data.values,
    texttemplate="%{text:.1f}%",
    textfont={"size": 10},
    hoverinfo='z+text',  # Fixed parameter name
    colorbar=dict(title="% Flagged (Alive Only)")
))

fig5.update_layout(
    title="SAM2 QC Flag Heatmap by Tricaine Concentration (Alive Embryos Only)",
    xaxis_title="SAM2 Flag Type",
    yaxis_title="Condition",
    height=400,
    width=800
)

# Save the heatmap
fig5.write_html(os.path.join(plot_dir, "sam2_flags_heatmap_alive_only.html"))
fig5.show()

print(f"\nUpdated plots saved (adjusted for alive embryos only):")
print("- sam2_individual_flags_analysis_alive_only.html (detailed trends over time)")
print("- sam2_flags_heatmap_alive_only.html (summary heatmap)")

print("\n=== KEY INSIGHT ===")
print("Now analyzing SAM2 QC flags ONLY for alive embryos to isolate")
print("movement-related vs death-related quality issues!")

=== SAM2 QC FLAGS SUMMARY BY CONDITION (ALIVE EMBRYOS ONLY) ===

SAM2 Flag Percentages by Condition (Alive Embryos Only):
          condition  n_total_observations  n_alive_observations  pct_alive  n_alive_embryos  HIGH_SEGMENTATION_VAR_SNIP_pct_alive  DISCONTINUOUS_MASK_pct_alive  MASK_ON_EDGE_pct_alive  SMALL_MASK_pct_alive
nan_tmem67_wildtype                  4117                  3190       77.5               22                                   4.9                           0.1                    10.0                   0.0
       tri_0_wik-ab                  1017                   312       30.7                9                                  49.7                           0.6                     0.0                   0.0
    tri_1-15_wik-ab                   904                   167       18.5                8                                   3.6                           0.0                     0.0                   0.0
    tri_1-20_wik-ab                  1921             


Updated plots saved (adjusted for alive embryos only):
- sam2_individual_flags_analysis_alive_only.html (detailed trends over time)
- sam2_flags_heatmap_alive_only.html (summary heatmap)

=== KEY INSIGHT ===
Now analyzing SAM2 QC flags ONLY for alive embryos to isolate
movement-related vs death-related quality issues!


In [17]:
# FOCUSED ANALYSIS: HIGH_SEGMENTATION_VAR_SNIP flag only
print("=== HIGH_SEGMENTATION_VAR_SNIP ANALYSIS ===\n")

# Check if this flag exists in our data
if 'sam2_HIGH_SEGMENTATION_VAR_SNIP_flag' in filtered_df.columns:
    high_seg_var_flag = 'sam2_HIGH_SEGMENTATION_VAR_SNIP_flag'
    print("Found HIGH_SEGMENTATION_VAR_SNIP flag in data")
else:
    print("Available SAM2 flag columns:")
    sam2_cols = [col for col in filtered_df.columns if col.startswith('sam2_') and col.endswith('_flag')]
    print(sam2_cols)
    
    # Check if it's in the top flags
    if 'HIGH_SEGMENTATION_VAR_SNIP' in top_flags:
        high_seg_var_flag = 'sam2_HIGH_SEGMENTATION_VAR_SNIP_flag'
        print("Using HIGH_SEGMENTATION_VAR_SNIP from top_flags")
    else:
        print("HIGH_SEGMENTATION_VAR_SNIP not found in top flags")
        print("Available top flags:", top_flags)
        # Let's use the first available flag as example
        if len(top_flags) > 0:
            high_seg_var_flag = f'sam2_{top_flags[0]}_flag'
            print(f"Using {top_flags[0]} as example instead")
        else:
            print("No SAM2 flags available")

=== HIGH_SEGMENTATION_VAR_SNIP ANALYSIS ===

Found HIGH_SEGMENTATION_VAR_SNIP flag in data


In [18]:
# Continue with HIGH_SEGMENTATION_VAR_SNIP analysis
if 'high_seg_var_flag' in locals():
    print(f"\nAnalyzing flag: {high_seg_var_flag}")
    
    # 1. Overall summary by condition (alive embryos only)
    print("\n=== SUMMARY BY CONDITION (ALIVE EMBRYOS ONLY) ===")
    high_seg_summary = []
    
    for condition in sorted(conditions):
        condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
        alive_data = condition_data[condition_data['dead_flag2'] == False]
        
        if len(alive_data) > 0:
            high_seg_pct = (alive_data[high_seg_var_flag].sum() / len(alive_data)) * 100
            high_seg_summary.append({
                'condition': condition,
                'n_alive_observations': len(alive_data),
                'n_alive_embryos': alive_data['embryo_id'].nunique(),
                'high_seg_var_pct': round(high_seg_pct, 1),
                'pct_alive': round((len(alive_data) / len(condition_data)) * 100, 1)
            })
    
    high_seg_df = pd.DataFrame(high_seg_summary)
    print(high_seg_df.to_string(index=False))
    
    # 2. Individual embryo scatter plot for HIGH_SEGMENTATION_VAR_SNIP
    fig_high_seg = go.Figure()
    
    for condition in sorted(conditions):
        condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
        alive_data = condition_data[condition_data['dead_flag2'] == False]
        
        if len(alive_data) > 0:
            # Create hover text
            hover_text = [
                f"<b>Condition: {condition}</b><br>"
                f"Embryo ID: {row['embryo_id']}<br>"
                f"Snip ID: {row['snip_id']}<br>"
                f"Stage (hpf): {row['predicted_stage_hpf']:.2f}<br>"
                f"High Seg Var: {row[high_seg_var_flag]}<br>"
                f"Frame: {row['frame_index']}"
                for _, row in alive_data.iterrows()
            ]
            
            fig_high_seg.add_trace(
                go.Scatter(
                    x=alive_data['predicted_stage_hpf'],
                    y=alive_data[high_seg_var_flag],
                    mode='markers',
                    marker=dict(
                        color=color_map[condition],
                        size=4,
                        opacity=0.6
                    ),
                    name=condition,
                    hovertemplate='%{text}<extra></extra>',
                    text=hover_text
                )
            )
    
    fig_high_seg.update_layout(
        title="HIGH_SEGMENTATION_VAR_SNIP Flag Over Time (Alive Embryos Only)",
        xaxis_title="Predicted Stage (hpf)",
        yaxis_title="High Segmentation Variance Flag (0=Good, 1=High Variance)",
        height=600,
        hovermode='closest'
    )
    
    # Save and show
    fig_high_seg.write_html(os.path.join(plot_dir, "high_segmentation_var_individual_trajectories.html"))
    fig_high_seg.show()
    
else:
    print("Could not proceed with HIGH_SEGMENTATION_VAR_SNIP analysis - flag not found")


Analyzing flag: sam2_HIGH_SEGMENTATION_VAR_SNIP_flag

=== SUMMARY BY CONDITION (ALIVE EMBRYOS ONLY) ===
          condition  n_alive_observations  n_alive_embryos  high_seg_var_pct  pct_alive
nan_tmem67_wildtype                  3190               22               4.9       77.5
       tri_0_wik-ab                   312                9              49.7       30.7
    tri_1-15_wik-ab                   167                8               3.6       18.5
    tri_1-20_wik-ab                   364               16               1.1       18.9
    tri_1-25_wik-ab                  1351               20              32.7       59.8
    tri_1-30_wik-ab                   880               19              26.9       41.0
    tri_1-35_wik-ab                   554               16               9.2       30.6
    tri_1-40_wik-ab                   824               15              22.1       42.9


In [19]:
# 3. Population trends for HIGH_SEGMENTATION_VAR_SNIP over time
if 'high_seg_var_flag' in locals():
    fig_high_seg_trends = go.Figure()
    
    for condition in sorted(conditions):
        condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
        
        bin_centers = []
        avg_high_seg_pct = []
        sample_sizes = []
        alive_sample_sizes = []
        
        for j in range(len(time_bins) - 1):
            bin_start, bin_end = time_bins[j], time_bins[j + 1]
            bin_data = condition_data[
                (condition_data['predicted_stage_hpf'] >= bin_start) & 
                (condition_data['predicted_stage_hpf'] < bin_end)
            ]
            
            # FILTER TO ALIVE EMBRYOS ONLY
            alive_bin_data = bin_data[bin_data['dead_flag2'] == False]
            
            if len(alive_bin_data) > 0:
                bin_centers.append((bin_start + bin_end) / 2)
                high_seg_pct = (alive_bin_data[high_seg_var_flag].sum() / len(alive_bin_data)) * 100
                avg_high_seg_pct.append(high_seg_pct)
                sample_sizes.append(len(bin_data))  # Total in bin
                alive_sample_sizes.append(len(alive_bin_data))  # Alive in bin
        
        # Create hover text
        hover_text = [
            f"<b>Condition: {condition}</b><br>"
            f"Time bin: {center:.1f} hpf<br>"
            f"% High Seg Var: {pct:.1f}%<br>"
            f"Alive embryos: {alive_n}<br>"
            f"Total observations: {total_n}"
            for center, pct, alive_n, total_n in zip(bin_centers, avg_high_seg_pct, alive_sample_sizes, sample_sizes)
        ]
        
        fig_high_seg_trends.add_trace(
            go.Scatter(
                x=bin_centers,
                y=avg_high_seg_pct,
                mode='lines+markers',
                line=dict(color=color_map[condition], width=3),
                marker=dict(size=8),
                name=condition,
                hovertemplate='%{text}<extra></extra>',
                text=hover_text
            )
        )
    
    fig_high_seg_trends.update_layout(
        title="HIGH_SEGMENTATION_VAR_SNIP Trends Over Time (Alive Embryos Only)",
        xaxis_title="Predicted Stage (hpf)",
        yaxis_title="% High Segmentation Variance",
        height=600,
        hovermode='closest',
        yaxis=dict(range=[0, 100])
    )
    
    # Save and show
    fig_high_seg_trends.write_html(os.path.join(plot_dir, "high_segmentation_var_population_trends.html"))
    fig_high_seg_trends.show()
    
    print(f"\nHIGH_SEGMENTATION_VAR_SNIP plots saved:")
    print("- high_segmentation_var_individual_trajectories.html")
    print("- high_segmentation_var_population_trends.html")
    
    print(f"\n=== KEY INSIGHT FOR HIGH_SEGMENTATION_VAR_SNIP ===")
    print("This flag likely indicates segmentation instability due to movement.")
    print("Lower tricaine = more movement = higher segmentation variance")
    print("Higher tricaine = less movement = lower segmentation variance")
    print("Compare trends to validate your movement hypothesis!")

else:
    print("HIGH_SEGMENTATION_VAR_SNIP analysis could not be completed")


HIGH_SEGMENTATION_VAR_SNIP plots saved:
- high_segmentation_var_individual_trajectories.html
- high_segmentation_var_population_trends.html

=== KEY INSIGHT FOR HIGH_SEGMENTATION_VAR_SNIP ===
This flag likely indicates segmentation instability due to movement.
Lower tricaine = more movement = higher segmentation variance
Higher tricaine = less movement = lower segmentation variance
Compare trends to validate your movement hypothesis!


In [20]:
# CRITICAL FILTER: Remove wells with multiple embryos
print("=== FILTERING FOR SINGLE-EMBRYO WELLS ONLY ===\n")

# Check embryo distribution per video_id
print("Before filtering - embryo distribution per video_id:")
embryo_per_video = filtered_df.groupby('video_id')['embryo_id'].nunique().sort_values(ascending=False)
print(f"Wells with >1 embryo: {(embryo_per_video > 1).sum()}")
print(f"Wells with 1 embryo: {(embryo_per_video == 1).sum()}")
print(f"Total wells: {len(embryo_per_video)}")

# Show examples of multi-embryo wells
multi_embryo_wells = embryo_per_video[embryo_per_video > 1]
if len(multi_embryo_wells) > 0:
    print(f"\nExample multi-embryo wells:")
    print(multi_embryo_wells.head(10))

# Filter to keep only wells with exactly 1 embryo
single_embryo_videos = embryo_per_video[embryo_per_video == 1].index
filtered_df_single = filtered_df[filtered_df['video_id'].isin(single_embryo_videos)].copy()

print(f"\nAfter filtering for single-embryo wells:")
print(f"Original data: {len(filtered_df)} observations")
print(f"Single-embryo data: {len(filtered_df_single)} observations")
print(f"Removed: {len(filtered_df) - len(filtered_df_single)} observations")

# Check embryo_id patterns (should all be _e01)
print(f"\nEmbryo ID patterns in single-embryo wells:")
embryo_patterns = filtered_df_single['embryo_id'].str.extract(r'.*_(e\d+)$')[0].value_counts()
print(embryo_patterns)

# Update our working dataset
filtered_df = filtered_df_single
print(f"\nUpdated working dataset: {len(filtered_df)} observations from single-embryo wells only")

=== FILTERING FOR SINGLE-EMBRYO WELLS ONLY ===

Before filtering - embryo distribution per video_id:
Wells with >1 embryo: 11
Wells with 1 embryo: 107
Total wells: 118

Example multi-embryo wells:
video_id
20250912_D04    2
20250912_F03    2
20250912_F05    2
20250912_F06    2
20250912_F07    2
20250912_F11    2
20250912_F12    2
20250912_G05    2
20250912_G06    2
20250912_G12    2
Name: embryo_id, dtype: int64

After filtering for single-embryo wells:
Original data: 16095 observations
Single-embryo data: 13609 observations
Removed: 2486 observations

Embryo ID patterns in single-embryo wells:
0
e01    13609
Name: count, dtype: int64

Updated working dataset: 13609 observations from single-embryo wells only


In [21]:
# RECOMPUTE: Population survival trends with single-embryo wells only
print("=== RECOMPUTING SURVIVAL TRENDS (SINGLE-EMBRYO WELLS ONLY) ===\n")

# Recalculate time bins for the filtered data
time_bins = np.arange(
    filtered_df['predicted_stage_hpf'].min(), 
    filtered_df['predicted_stage_hpf'].max() + 5, 
    5  # 5 hpf bins
)

fig2_corrected = go.Figure()

# Calculate average % dead for each condition over time bins (corrected)
for condition in sorted(conditions):
    condition_data = filtered_df[filtered_df['chem_n_genotype'] == condition]
    
    bin_centers = []
    avg_dead_pct = []
    sample_sizes = []
    
    for i in range(len(time_bins) - 1):
        bin_start, bin_end = time_bins[i], time_bins[i + 1]
        bin_data = condition_data[
            (condition_data['predicted_stage_hpf'] >= bin_start) & 
            (condition_data['predicted_stage_hpf'] < bin_end)
        ]
        
        if len(bin_data) > 0:
            bin_centers.append((bin_start + bin_end) / 2)
            dead_pct = (bin_data['dead_flag2'].sum() / len(bin_data)) * 100
            avg_dead_pct.append(dead_pct)
            sample_sizes.append(len(bin_data))
    
    # Create hover text for line plot
    hover_text = [
        f"<b>Condition: {condition}</b><br>"
        f"Time bin: {center:.1f} hpf<br>"
        f"% Dead: {pct:.1f}%<br>"
        f"Sample size: {n} observations<br>"
        f"(Single-embryo wells only)"
        for center, pct, n in zip(bin_centers, avg_dead_pct, sample_sizes)
    ]
    
    fig2_corrected.add_trace(
        go.Scatter(
            x=bin_centers,
            y=avg_dead_pct,
            mode='lines+markers',
            line=dict(color=color_map[condition], width=3),
            marker=dict(size=8),
            name=condition,
            hovertemplate='%{text}<extra></extra>',
            text=hover_text
        )
    )

fig2_corrected.update_layout(
    title="Population Survival Trends: Average % Dead Over Time (Single-Embryo Wells Only)",
    xaxis_title="Predicted Stage (hpf)",
    yaxis_title="Average % Dead",
    height=600,
    hovermode='closest',
    yaxis=dict(range=[0, 100])  # Set y-axis to 0-100%
)

# Save the corrected plot
fig2_corrected.write_html(os.path.join(plot_dir, "population_survival_trends_single_embryo_corrected.html"))
fig2_corrected.show()

# Summary of correction impact
print(f"\nCorrected survival analysis saved:")
print("- population_survival_trends_single_embryo_corrected.html")
print("\nThis removes confounding effects from multi-embryo wells where")
print("tricaine concentration affects multiple embryos per well differently!")

=== RECOMPUTING SURVIVAL TRENDS (SINGLE-EMBRYO WELLS ONLY) ===




Corrected survival analysis saved:
- population_survival_trends_single_embryo_corrected.html

This removes confounding effects from multi-embryo wells where
tricaine concentration affects multiple embryos per well differently!


In [22]:
# ANALYZE MULTI-EMBRYO WELLS - The Fun Stuff! 
print("=== MULTI-EMBRYO WELLS ANALYSIS ===\n")

# Get the multi-embryo wells we filtered out earlier
embryo_per_video = qc_staged_df.groupby('video_id')['embryo_id'].nunique().sort_values(ascending=False)
multi_embryo_videos = embryo_per_video[embryo_per_video > 1].index

# Filter for tricaine + wildtype in multi-embryo wells
tricane_conditions = qc_staged_df['chem_perturbation'].str.startswith('tri_', na=False)
wildtype_control = qc_staged_df['chem_n_genotype'] == 'nan_tmem67_wildtype'
multi_embryo_df = qc_staged_df[
    (qc_staged_df['video_id'].isin(multi_embryo_videos)) & 
    (tricane_conditions | wildtype_control)
].copy()

print(f"Multi-embryo wells data: {len(multi_embryo_df)} observations")
print(f"Number of multi-embryo wells: {multi_embryo_df['video_id'].nunique()}")
print(f"Embryos per well distribution:")
multi_embryo_counts = multi_embryo_df.groupby('video_id')['embryo_id'].nunique().value_counts().sort_index()
print(multi_embryo_counts)

# Show embryo patterns in multi-embryo wells
print(f"\nEmbryo ID patterns in multi-embryo wells:")
embryo_patterns = multi_embryo_df['embryo_id'].str.extract(r'.*_(e\d+)$')[0].value_counts().sort_index()
print(embryo_patterns)

=== MULTI-EMBRYO WELLS ANALYSIS ===

Multi-embryo wells data: 2486 observations
Number of multi-embryo wells: 11
Embryos per well distribution:
embryo_id
2    11
Name: count, dtype: int64

Embryo ID patterns in multi-embryo wells:
0
e01    1243
e02    1243
Name: count, dtype: int64


In [23]:
# INTER-EMBRYO DYNAMICS: Compare survival between embryos in the same well
print("=== INTER-EMBRYO DYNAMICS ANALYSIS ===\n")

# For each multi-embryo well, compare survival rates between embryos
well_survival_comparison = []

for video_id in multi_embryo_df['video_id'].unique():
    well_data = multi_embryo_df[multi_embryo_df['video_id'] == video_id]
    condition = well_data['chem_n_genotype'].iloc[0]
    
    embryo_survival = {}
    for embryo_id in well_data['embryo_id'].unique():
        embryo_data = well_data[well_data['embryo_id'] == embryo_id]
        pct_dead = (embryo_data['dead_flag2'].sum() / len(embryo_data)) * 100
        embryo_survival[embryo_id] = pct_dead
    
    # Calculate survival variance within the well
    survival_rates = list(embryo_survival.values())
    survival_variance = np.var(survival_rates) if len(survival_rates) > 1 else 0
    
    well_survival_comparison.append({
        'video_id': video_id,
        'condition': condition,
        'n_embryos': len(embryo_survival),
        'avg_pct_dead': np.mean(survival_rates),
        'survival_variance': survival_variance,
        'embryo_survival': embryo_survival
    })

survival_df = pd.DataFrame(well_survival_comparison)
print("Multi-embryo well survival comparison:")
print(survival_df[['video_id', 'condition', 'n_embryos', 'avg_pct_dead', 'survival_variance']].head(10))

# Group by condition to see patterns
print(f"\nSurvival variance by condition (shows embryo-to-embryo differences):")
condition_variance = survival_df.groupby('condition')['survival_variance'].agg(['mean', 'std', 'count']).round(2)
print(condition_variance)

=== INTER-EMBRYO DYNAMICS ANALYSIS ===

Multi-embryo well survival comparison:
       video_id        condition  n_embryos  avg_pct_dead  survival_variance
0  20250912_D04  tri_1-25_wik-ab          2     90.707965          15.858720
1  20250912_F03  tri_1-20_wik-ab          2     78.761062           7.048320
2  20250912_F05  tri_1-25_wik-ab          2     93.805310          19.578667
3  20250912_F06  tri_1-30_wik-ab          2     67.256637           0.000000
4  20250912_F07  tri_1-30_wik-ab          2     53.097345           0.000000
5  20250912_F11  tri_1-40_wik-ab          2     96.460177          12.530347
6  20250912_F12     tri_0_wik-ab          2     96.902655           0.195787
7  20250912_G05  tri_1-25_wik-ab          2      0.000000           0.000000
8  20250912_G06  tri_1-30_wik-ab          2      0.000000           0.000000
9  20250912_G12     tri_0_wik-ab          2     89.380531           0.000000

Survival variance by condition (shows embryo-to-embryo differences):
    

In [24]:
# SIMPLE: % Average Dead Over Time for Multi-Embryo Wells
print("=== MULTI-EMBRYO WELLS: % DEAD OVER TIME ===\n")

# Create time bins for multi-embryo data
time_bins = np.arange(
    multi_embryo_df['predicted_stage_hpf'].min(), 
    multi_embryo_df['predicted_stage_hpf'].max() + 5, 
    5  # 5 hpf bins
)

fig_multi = go.Figure()

# Get color map (reuse from single-embryo analysis)
multi_conditions = multi_embryo_df['chem_n_genotype'].unique()
multi_color_map = {condition: px.colors.qualitative.Plotly[i % len(px.colors.qualitative.Plotly)] 
                   for i, condition in enumerate(sorted(multi_conditions))}

# Calculate average % dead for each condition over time bins
for condition in sorted(multi_conditions):
    condition_data = multi_embryo_df[multi_embryo_df['chem_n_genotype'] == condition]
    
    bin_centers = []
    avg_dead_pct = []
    sample_sizes = []
    
    for i in range(len(time_bins) - 1):
        bin_start, bin_end = time_bins[i], time_bins[i + 1]
        bin_data = condition_data[
            (condition_data['predicted_stage_hpf'] >= bin_start) & 
            (condition_data['predicted_stage_hpf'] < bin_end)
        ]
        
        if len(bin_data) > 0:
            bin_centers.append((bin_start + bin_end) / 2)
            dead_pct = (bin_data['dead_flag2'].sum() / len(bin_data)) * 100
            avg_dead_pct.append(dead_pct)
            sample_sizes.append(len(bin_data))
    
    # Create hover text
    hover_text = [
        f"<b>Condition: {condition}</b><br>"
        f"Time bin: {center:.1f} hpf<br>"
        f"% Dead: {pct:.1f}%<br>"
        f"Sample size: {n} observations<br>"
        f"(Multi-embryo wells)"
        for center, pct, n in zip(bin_centers, avg_dead_pct, sample_sizes)
    ]
    
    fig_multi.add_trace(
        go.Scatter(
            x=bin_centers,
            y=avg_dead_pct,
            mode='lines+markers',
            line=dict(color=multi_color_map[condition], width=3),
            marker=dict(size=8),
            name=condition,
            hovertemplate='%{text}<extra></extra>',
            text=hover_text
        )
    )

fig_multi.update_layout(
    title="Population Survival Trends: Average % Dead Over Time (Multi-Embryo Wells)",
    xaxis_title="Predicted Stage (hpf)",
    yaxis_title="Average % Dead",
    height=600,
    hovermode='closest',
    yaxis=dict(range=[0, 100])
)

# Save the plot
fig_multi.write_html(os.path.join(plot_dir, "population_survival_trends_multi_embryo.html"))
fig_multi.show()

print(f"\nMulti-embryo survival trends saved:")
print("- population_survival_trends_multi_embryo.html")
print(f"Data: {len(multi_embryo_df)} observations from {multi_embryo_df['video_id'].nunique()} multi-embryo wells")

=== MULTI-EMBRYO WELLS: % DEAD OVER TIME ===




Multi-embryo survival trends saved:
- population_survival_trends_multi_embryo.html
Data: 2486 observations from 11 multi-embryo wells


In [25]:
# INDIVIDUAL ANALYSIS: use_embryo_flag
print("=== USE_EMBRYO_FLAG INDIVIDUAL ANALYSIS ===\n")

# Use the filtered_df (should be single-embryo wells if you ran the filtering)
# If not, we'll work with whatever filtered_df is available

# Check what data we're working with
try:
    print(f"Working with filtered_df: {len(filtered_df)} observations")
    data_to_use = filtered_df
    data_description = "filtered data"
except NameError:
    print("filtered_df not available, using multi_embryo_df")
    data_to_use = multi_embryo_df
    data_description = "multi-embryo data"

# Create time bins
time_bins = np.arange(
    data_to_use['predicted_stage_hpf'].min(), 
    data_to_use['predicted_stage_hpf'].max() + 5, 
    5  # 5 hpf bins
)

fig_use_embryo = go.Figure()

# Get conditions and color map
use_embryo_conditions = data_to_use['chem_n_genotype'].unique()
use_embryo_color_map = {condition: px.colors.qualitative.Plotly[i % len(px.colors.qualitative.Plotly)] 
                        for i, condition in enumerate(sorted(use_embryo_conditions))}

# Calculate average % use_embryo_flag for each condition over time bins
for condition in sorted(use_embryo_conditions):
    condition_data = data_to_use[data_to_use['chem_n_genotype'] == condition]
    
    bin_centers = []
    avg_use_embryo_pct = []
    sample_sizes = []
    
    for i in range(len(time_bins) - 1):
        bin_start, bin_end = time_bins[i], time_bins[i + 1]
        bin_data = condition_data[
            (condition_data['predicted_stage_hpf'] >= bin_start) & 
            (condition_data['predicted_stage_hpf'] < bin_end)
        ]
        
        if len(bin_data) > 0:
            bin_centers.append((bin_start + bin_end) / 2)
            use_embryo_pct = (bin_data['use_embryo_flag'].sum() / len(bin_data)) * 100
            avg_use_embryo_pct.append(use_embryo_pct)
            sample_sizes.append(len(bin_data))
    
    # Create hover text
    hover_text = [
        f"<b>Condition: {condition}</b><br>"
        f"Time bin: {center:.1f} hpf<br>"
        f"% Use Embryo: {pct:.1f}%<br>"
        f"Sample size: {n} observations<br>"
        f"({data_description})"
        for center, pct, n in zip(bin_centers, avg_use_embryo_pct, sample_sizes)
    ]
    
    fig_use_embryo.add_trace(
        go.Scatter(
            x=bin_centers,
            y=avg_use_embryo_pct,
            mode='lines+markers',
            line=dict(color=use_embryo_color_map[condition], width=3),
            marker=dict(size=8),
            name=condition,
            hovertemplate='%{text}<extra></extra>',
            text=hover_text
        )
    )

fig_use_embryo.update_layout(
    title="Use Embryo Flag Trends Over Time by Tricaine Concentration",
    xaxis_title="Predicted Stage (hpf)",
    yaxis_title="% Use Embryo Flag",
    height=600,
    hovermode='closest',
    yaxis=dict(range=[0, 100])
)

# Save the plot
fig_use_embryo.write_html(os.path.join(plot_dir, "use_embryo_flag_individual_analysis.html"))
fig_use_embryo.show()

print(f"\nUse embryo flag analysis saved:")
print("- use_embryo_flag_individual_analysis.html")
print(f"\nThis shows the % of observations marked as 'usable' over time")
print("Higher % = better overall embryo quality for analysis")
print("Lower tricaine might reduce usability due to movement artifacts")

=== USE_EMBRYO_FLAG INDIVIDUAL ANALYSIS ===

Working with filtered_df: 13609 observations



Use embryo flag analysis saved:
- use_embryo_flag_individual_analysis.html

This shows the % of observations marked as 'usable' over time
Higher % = better overall embryo quality for analysis
Lower tricaine might reduce usability due to movement artifacts


In [26]:
# USE_EMBRYO_FLAG ANALYSIS - ADJUSTED FOR ALIVE EMBRYOS ONLY
print("=== USE_EMBRYO_FLAG ANALYSIS (ALIVE EMBRYOS ONLY) ===\n")

# Check what data we're working with
try:
    print(f"Working with filtered_df: {len(filtered_df)} observations")
    data_to_use = filtered_df
    data_description = "filtered data"
except NameError:
    print("filtered_df not available, using multi_embryo_df")
    data_to_use = multi_embryo_df
    data_description = "multi-embryo data"

# Create time bins
time_bins = np.arange(
    data_to_use['predicted_stage_hpf'].min(), 
    data_to_use['predicted_stage_hpf'].max() + 5, 
    5  # 5 hpf bins
)

fig_use_embryo_alive = go.Figure()

# Get conditions and color map
use_embryo_conditions = data_to_use['chem_n_genotype'].unique()
use_embryo_color_map = {condition: px.colors.qualitative.Plotly[i % len(px.colors.qualitative.Plotly)] 
                        for i, condition in enumerate(sorted(use_embryo_conditions))}

# Calculate average % use_embryo_flag for ALIVE embryos only
for condition in sorted(use_embryo_conditions):
    condition_data = data_to_use[data_to_use['chem_n_genotype'] == condition]
    
    bin_centers = []
    avg_use_embryo_pct = []
    sample_sizes = []
    alive_sample_sizes = []
    
    for i in range(len(time_bins) - 1):
        bin_start, bin_end = time_bins[i], time_bins[i + 1]
        bin_data = condition_data[
            (condition_data['predicted_stage_hpf'] >= bin_start) & 
            (condition_data['predicted_stage_hpf'] < bin_end)
        ]
        
        # FILTER TO ALIVE EMBRYOS ONLY
        alive_bin_data = bin_data[bin_data['dead_flag2'] == False]
        
        if len(alive_bin_data) > 0:
            bin_centers.append((bin_start + bin_end) / 2)
            use_embryo_pct = (alive_bin_data['use_embryo_flag'].sum() / len(alive_bin_data)) * 100
            avg_use_embryo_pct.append(use_embryo_pct)
            sample_sizes.append(len(bin_data))  # Total in bin
            alive_sample_sizes.append(len(alive_bin_data))  # Alive in bin
    
    # Create hover text with alive vs total info
    hover_text = [
        f"<b>Condition: {condition}</b><br>"
        f"Time bin: {center:.1f} hpf<br>"
        f"% Use Embryo (Alive Only): {pct:.1f}%<br>"
        f"Alive embryos: {alive_n}<br>"
        f"Total observations: {total_n}<br>"
        f"({data_description})"
        for center, pct, alive_n, total_n in zip(bin_centers, avg_use_embryo_pct, alive_sample_sizes, sample_sizes)
    ]
    
    fig_use_embryo_alive.add_trace(
        go.Scatter(
            x=bin_centers,
            y=avg_use_embryo_pct,
            mode='lines+markers',
            line=dict(color=use_embryo_color_map[condition], width=3),
            marker=dict(size=8),
            name=condition,
            hovertemplate='%{text}<extra></extra>',
            text=hover_text
        )
    )

fig_use_embryo_alive.update_layout(
    title="Use Embryo Flag Trends Over Time by Tricaine Concentration (Alive Embryos Only)",
    xaxis_title="Predicted Stage (hpf)",
    yaxis_title="% Use Embryo Flag (Alive Only)",
    height=600,
    hovermode='closest',
    yaxis=dict(range=[0, 100])
)

# Save the plot
fig_use_embryo_alive.write_html(os.path.join(plot_dir, "use_embryo_flag_alive_only_analysis.html"))
fig_use_embryo_alive.show()

print(f"\nUse embryo flag analysis (alive only) saved:")
print("- use_embryo_flag_alive_only_analysis.html")
print(f"\n=== KEY INSIGHT ===")
print("Now shows usability of LIVING embryos only - isolates movement")
print("effects from death effects on data quality!")
print("Higher tricaine should show better usability in surviving embryos")

=== USE_EMBRYO_FLAG ANALYSIS (ALIVE EMBRYOS ONLY) ===

Working with filtered_df: 13609 observations



Use embryo flag analysis (alive only) saved:
- use_embryo_flag_alive_only_analysis.html

=== KEY INSIGHT ===
Now shows usability of LIVING embryos only - isolates movement
effects from death effects on data quality!
Higher tricaine should show better usability in surviving embryos


In [27]:
# TOP 3 LONGEST LIVING EMBRYOS PER CONDITION
print("=== TOP 3 LONGEST LIVING EMBRYOS PER CONDITION ===\n")

# Check what data we're working with
try:
    data_to_use = filtered_df
    print(f"Using filtered_df: {len(data_to_use)} observations")
except NameError:
    try:
        data_to_use = multi_embryo_df
        print(f"Using multi_embryo_df: {len(data_to_use)} observations")
    except NameError:
        data_to_use = qc_staged_df
        print(f"Using qc_staged_df: {len(data_to_use)} observations")

# Filter for alive embryos only
alive_data = data_to_use[data_to_use['dead_flag2'] == False].copy()

# Get max stage reached per embryo (for alive embryos only)
embryo_max_stages = alive_data.groupby(['chem_n_genotype', 'embryo_id'])['predicted_stage_hpf'].max().reset_index()

# Get top 3 longest living embryos per condition
for condition in sorted(embryo_max_stages['chem_n_genotype'].unique()):
    condition_embryos = embryo_max_stages[embryo_max_stages['chem_n_genotype'] == condition]
    top3 = condition_embryos.nlargest(3, 'predicted_stage_hpf')
    
    print(f"🏆 {condition}:")
    for i, (_, row) in enumerate(top3.iterrows(), 1):
        print(f"  {i}. {row['embryo_id']} - {row['predicted_stage_hpf']:.1f} hpf")
    print()

=== TOP 3 LONGEST LIVING EMBRYOS PER CONDITION ===

Using filtered_df: 13609 observations
🏆 nan_tmem67_wildtype:
  1. 20250711_B08_e01 - 127.9 hpf
  2. 20250711_D03_e01 - 127.9 hpf
  3. 20250711_E05_e01 - 127.9 hpf

🏆 tri_0_wik-ab:
  1. 20250912_D12_e01 - 110.1 hpf
  2. 20250912_E12_e01 - 110.1 hpf
  3. 20250912_C12_e01 - 28.8 hpf

🏆 tri_1-15_wik-ab:
  1. 20250912_D01_e01 - 53.5 hpf
  2. 20250912_C01_e01 - 40.3 hpf
  3. 20250912_A01_e01 - 37.6 hpf

🏆 tri_1-20_wik-ab:
  1. 20250912_C03_e01 - 95.0 hpf
  2. 20250912_A02_e01 - 57.0 hpf
  3. 20250912_D03_e01 - 50.0 hpf

🏆 tri_1-25_wik-ab:
  1. 20250912_A04_e01 - 110.1 hpf
  2. 20250912_B05_e01 - 110.1 hpf
  3. 20250912_C04_e01 - 110.1 hpf

🏆 tri_1-30_wik-ab:
  1. 20250912_C06_e01 - 110.1 hpf
  2. 20250912_E06_e01 - 110.1 hpf
  3. 20250912_A07_e01 - 61.4 hpf

🏆 tri_1-35_wik-ab:
  1. 20250912_E08_e01 - 110.1 hpf
  2. 20250912_D08_e01 - 103.9 hpf
  3. 20250912_B08_e01 - 91.5 hpf

🏆 tri_1-40_wik-ab:
  1. 20250912_A10_e01 - 110.1 hpf
  2. 202509

In [28]:
# EMBRYO MOVEMENT OVER TIME ANALYSIS - Direct measurement using xpos/ypos
print("=== EMBRYO MOVEMENT OVER DEVELOPMENTAL TIME ===\n")

# Check what data we're working with
try:
    data_to_use = filtered_df
    print(f"Using filtered_df: {len(data_to_use)} observations")
except NameError:
    try:
        data_to_use = multi_embryo_df
        print(f"Using multi_embryo_df: {len(data_to_use)} observations")
    except NameError:
        data_to_use = qc_staged_df
        print(f"Using qc_staged_df: {len(data_to_use)} observations")

# Filter for alive embryos only
alive_data = data_to_use[data_to_use['dead_flag2'] == False].copy()
print(f"Analyzing movement for {len(alive_data)} alive observations")

# Calculate frame-to-frame movement for each embryo
movement_time_data = []

for embryo_id in alive_data['embryo_id'].unique():
    embryo_data = alive_data[alive_data['embryo_id'] == embryo_id].sort_values('predicted_stage_hpf')
    
    if len(embryo_data) < 2:  # Need at least 2 points
        continue
    
    condition = embryo_data['chem_n_genotype'].iloc[0]
    
    # Calculate movement for each time point
    for i in range(1, len(embryo_data)):
        prev_row = embryo_data.iloc[i-1]
        curr_row = embryo_data.iloc[i]
        
        # Calculate Euclidean distance moved
        movement = np.sqrt((curr_row['xpos'] - prev_row['xpos'])**2 + 
                          (curr_row['ypos'] - prev_row['ypos'])**2)
        
        movement_time_data.append({
            'embryo_id': embryo_id,
            'condition': condition,
            'predicted_stage_hpf': curr_row['predicted_stage_hpf'],
            'movement': movement,
            'time_interval': curr_row['predicted_stage_hpf'] - prev_row['predicted_stage_hpf']
        })

movement_time_df = pd.DataFrame(movement_time_data)
print(f"Calculated {len(movement_time_df)} movement measurements across time")
print(f"Conditions: {sorted(movement_time_df['condition'].unique())}")

=== EMBRYO MOVEMENT OVER DEVELOPMENTAL TIME ===

Using filtered_df: 13609 observations
Analyzing movement for 6662 alive observations
Calculated 6558 movement measurements across time
Conditions: ['nan_tmem67_wildtype', 'tri_0_wik-ab', 'tri_1-15_wik-ab', 'tri_1-20_wik-ab', 'tri_1-25_wik-ab', 'tri_1-30_wik-ab', 'tri_1-35_wik-ab', 'tri_1-40_wik-ab']


In [29]:
# TIME-BINNED MOVEMENT ANALYSIS with error bars
print("=== TIME-BINNED MOVEMENT ANALYSIS ===\n")

# Create time bins
time_bins = np.arange(
    movement_time_df['predicted_stage_hpf'].min(), 
    movement_time_df['predicted_stage_hpf'].max() + 5, 
    5  # 5 hpf bins
)

print(f"Time bins: {time_bins[0]:.1f} to {time_bins[-1]:.1f} hpf")

# Calculate movement statistics for each condition and time bin
movement_stats_by_time = []

conditions = sorted(movement_time_df['condition'].unique())
for condition in conditions:
    condition_data = movement_time_df[movement_time_df['condition'] == condition]
    
    for i in range(len(time_bins) - 1):
        bin_start, bin_end = time_bins[i], time_bins[i + 1]
        bin_data = condition_data[
            (condition_data['predicted_stage_hpf'] >= bin_start) & 
            (condition_data['predicted_stage_hpf'] < bin_end)
        ]
        
        if len(bin_data) > 0:
            bin_center = (bin_start + bin_end) / 2
            
            movement_stats_by_time.append({
                'condition': condition,
                'time_bin_center': bin_center,
                'time_bin_start': bin_start,
                'time_bin_end': bin_end,
                'mean_movement': bin_data['movement'].mean(),
                'std_movement': bin_data['movement'].std(),
                'sem_movement': bin_data['movement'].sem(),  # Standard error of mean
                'n_observations': len(bin_data),
                'n_embryos': bin_data['embryo_id'].nunique()
            })

movement_stats_df = pd.DataFrame(movement_stats_by_time)
print(f"Created {len(movement_stats_df)} time-binned movement statistics")

# Show sample of the data
print("\nSample movement statistics:")
print(movement_stats_df.head(10))

=== TIME-BINNED MOVEMENT ANALYSIS ===

Time bins: 7.6 to 132.6 hpf
Created 158 time-binned movement statistics

Sample movement statistics:
             condition  time_bin_center  time_bin_start  time_bin_end  \
0  nan_tmem67_wildtype        10.089872        7.589872     12.589872   
1  nan_tmem67_wildtype        15.089872       12.589872     17.589872   
2  nan_tmem67_wildtype        20.089872       17.589872     22.589872   
3  nan_tmem67_wildtype        25.089872       22.589872     27.589872   
4  nan_tmem67_wildtype        30.089872       27.589872     32.589872   
5  nan_tmem67_wildtype        35.089872       32.589872     37.589872   
6  nan_tmem67_wildtype        40.089872       37.589872     42.589872   
7  nan_tmem67_wildtype        45.089872       42.589872     47.589872   
8  nan_tmem67_wildtype        50.089872       47.589872     52.589872   
9  nan_tmem67_wildtype        55.089872       52.589872     57.589872   

   mean_movement  std_movement  sem_movement  n_observat

In [30]:
# LINE PLOT: Movement trends over developmental time with error bars
print("=== MOVEMENT TRENDS LINE PLOT ===\n")

fig_movement_time = go.Figure()

# Create color map
movement_color_map = {condition: px.colors.qualitative.Plotly[i % len(px.colors.qualitative.Plotly)] 
                      for i, condition in enumerate(conditions)}

# Plot each condition
for condition in conditions:
    condition_stats = movement_stats_df[movement_stats_df['condition'] == condition].sort_values('time_bin_center')
    
    if len(condition_stats) > 0:
        # Create hover text
        hover_text = [
            f"<b>Condition: {condition}</b><br>"
            f"Time: {time:.1f} hpf<br>"
            f"Mean Movement: {movement:.3f} pixels<br>"
            f"SEM: {sem:.3f}<br>"
            f"N observations: {n_obs}<br>"
            f"N embryos: {n_emb}"
            for time, movement, sem, n_obs, n_emb in zip(
                condition_stats['time_bin_center'],
                condition_stats['mean_movement'], 
                condition_stats['sem_movement'],
                condition_stats['n_observations'],
                condition_stats['n_embryos']
            )
        ]
        
        fig_movement_time.add_trace(
            go.Scatter(
                x=condition_stats['time_bin_center'],
                y=condition_stats['mean_movement'],
                error_y=dict(
                    type='data',
                    array=condition_stats['sem_movement'],
                    visible=True,
                    thickness=2,
                    width=3
                ),
                mode='lines+markers',
                line=dict(color=movement_color_map[condition], width=3),
                marker=dict(size=8, color=movement_color_map[condition]),
                name=condition,
                hovertemplate='%{text}<extra></extra>',
                text=hover_text
            )
        )

fig_movement_time.update_layout(
    title="Embryo Movement Over Developmental Time by Tricaine Concentration (Alive Embryos)",
    xaxis_title="Predicted Stage (hpf)",
    yaxis_title="Average Movement (pixels per frame)",
    height=600,
    hovermode='closest',
    legend=dict(
        x=0.02,
        y=0.98,
        bordercolor="Black",
        borderwidth=1
    )
)

# Save the plot
fig_movement_time.write_html(os.path.join(plot_dir, "embryo_movement_over_time_with_errorbars.html"))
fig_movement_time.show()

print(f"\nMovement over time analysis saved:")
print("- embryo_movement_over_time_with_errorbars.html")

# Summary statistics
print(f"\n=== MOVEMENT ANALYSIS SUMMARY ===")
overall_stats = movement_stats_df.groupby('condition').agg({
    'mean_movement': ['mean', 'std'],
    'n_observations': 'sum',
    'n_embryos': 'sum'
}).round(4)

print("Overall movement by condition:")
print(overall_stats)

print(f"\n=== KEY INSIGHTS ===")
print("✅ Direct measurement of embryo position changes over time")
print("✅ Error bars show variability at each time point") 
print("✅ Should show: Lower tricaine = Higher movement")
print("✅ Should show: Higher tricaine = Lower movement")
print("✅ Validates tricaine effectiveness for imaging quality!")

=== MOVEMENT TRENDS LINE PLOT ===




Movement over time analysis saved:
- embryo_movement_over_time_with_errorbars.html

=== MOVEMENT ANALYSIS SUMMARY ===
Overall movement by condition:
                    mean_movement         n_observations n_embryos
                             mean     std            sum       sum
condition                                                         
nan_tmem67_wildtype        0.0202  0.0390           3168       375
tri_0_wik-ab               0.0810  0.0390            276        55
tri_1-15_wik-ab            0.0044  0.0017            159        38
tri_1-20_wik-ab            0.0034  0.0017            302        68
tri_1-25_wik-ab            0.0889  0.0621            852       165
tri_1-30_wik-ab            0.0882  0.0784            461        96
tri_1-35_wik-ab            0.0114  0.0102            538       116
tri_1-40_wik-ab            0.0649  0.0438            802       157

=== KEY INSIGHTS ===
✅ Direct measurement of embryo position changes over time
✅ Error bars show variability at 

In [31]:
# EMBRYO MOVEMENT ANALYSIS - Track actual position changes over time
print("=== EMBRYO MOVEMENT ANALYSIS ===\n")

# Check what data we're working with
try:
    data_to_use = filtered_df
    print(f"Using filtered_df: {len(data_to_use)} observations")
except NameError:
    try:
        data_to_use = multi_embryo_df
        print(f"Using multi_embryo_df: {len(data_to_use)} observations")
    except NameError:
        data_to_use = qc_staged_df
        print(f"Using qc_staged_df: {len(data_to_use)} observations")

# Filter for alive embryos only
alive_data = data_to_use[data_to_use['dead_flag2'] == False].copy()

print(f"Analyzing movement for {len(alive_data)} alive observations")
print(f"Unique embryos: {alive_data['embryo_id'].nunique()}")

# Calculate movement per embryo
embryo_movement_data = []

for embryo_id in alive_data['embryo_id'].unique():
    embryo_data = alive_data[alive_data['embryo_id'] == embryo_id].sort_values('predicted_stage_hpf')
    
    if len(embryo_data) < 2:  # Need at least 2 points to calculate movement
        continue
    
    # Calculate frame-to-frame movement
    movements = []
    for i in range(1, len(embryo_data)):
        prev_x, prev_y = embryo_data.iloc[i-1]['xpos'], embryo_data.iloc[i-1]['ypos']
        curr_x, curr_y = embryo_data.iloc[i]['xpos'], embryo_data.iloc[i]['ypos']
        
        # Calculate Euclidean distance moved
        movement = np.sqrt((curr_x - prev_x)**2 + (curr_y - prev_y)**2)
        movements.append(movement)
    
    if movements:  # Only if we have movement data
        embryo_movement_data.append({
            'embryo_id': embryo_id,
            'condition': embryo_data['chem_n_genotype'].iloc[0],
            'avg_movement': np.mean(movements),
            'std_movement': np.std(movements),
            'max_movement': np.max(movements),
            'n_frames': len(movements),
            'total_displacement': np.sum(movements)
        })

movement_df = pd.DataFrame(embryo_movement_data)
print(f"\nMovement analysis for {len(movement_df)} embryos with sufficient data")

# Summary by condition
print("\nAverage movement by condition:")
movement_summary = movement_df.groupby('condition').agg({
    'avg_movement': ['mean', 'std', 'count'],
    'max_movement': ['mean', 'std'],
    'total_displacement': ['mean', 'std']
}).round(3)

print(movement_summary)

=== EMBRYO MOVEMENT ANALYSIS ===

Using filtered_df: 13609 observations
Analyzing movement for 6662 alive observations
Unique embryos: 104



Movement analysis for 101 embryos with sufficient data

Average movement by condition:
                    avg_movement              max_movement         \
                            mean    std count         mean    std   
condition                                                           
nan_tmem67_wildtype        0.010  0.031    22        0.081  0.119   
tri_0_wik-ab               0.051  0.030     5        0.166  0.105   
tri_1-15_wik-ab            0.005  0.002     8        0.016  0.013   
tri_1-20_wik-ab            0.006  0.003    12        0.014  0.006   
tri_1-25_wik-ab            0.056  0.046    12        0.315  0.298   
tri_1-30_wik-ab            0.028  0.038    13        0.120  0.247   
tri_1-35_wik-ab            0.010  0.005    16        0.043  0.047   
tri_1-40_wik-ab            0.041  0.034    13        0.205  0.239   

                    total_displacement         
                                  mean    std  
condition                                      
nan_tmem